In [13]:
import os
import pandas as pd
from aesim.simba import ProjectRepository
from bokeh.plotting import figure, show, row, output_notebook

# JMAG-RT PMSM model validation

## Objective

Validation of the JMAG-RT lookup table model by comparing simulation results from JMAG FEA software with SIMBA.

## JMAG-RT Model

The model incorporates key parameters such as Flux, Torque, Advance Angle, and Rotor Angle, which are essential in simulating spatial harmonics and non-linearities and thus to reflect different motor behaviors such as torque ripple or magnetic saturation.

The JMAG-RT model used in this example was generated from the FEA model in 1 hour 20 minutes. The FEA model incorporates more than 8000 elements, whereas the RT model is defined by 12 Current points, 73 Advance Angle points and 121 Rotor Position points.

## Simulation circuit

In order to focus solely on the comparison of the model and not take into account other factors, like control etc., a very simple circuit was used:

![JMAG-RT Validation](fig/jmag-rt_validation.png)

The circuit consists of a JMAG-RT PMSM motor fed directly from an ideal three-phase voltage source. The motor is connected to a load that imposes a constant speed of 500 rpm.

**!!! To run the circuit simulation, please the change the path of the .rtt file in the SIMBA design.**

In [14]:
# Read the CSV file into a DataFrame
data_FEA = pd.read_csv(os.path.join(os.getcwd(), "data","torque_current_jmag.csv"))
path_RTT = os.path.join(os.getcwd(), "data","20220613_SPMServo.rtt")

# Read the .jsimba file
project = ProjectRepository(os.path.join(os.getcwd(), 'jmag-rt_validation.jsimba'))
design = project.GetDesignByName('JMAG-RT Validation')
pmsm = design.Circuit.GetDeviceByName("JmagRT_PMSM")
pmsm.RttFilePath.UserValue = path_RTT

In [15]:
# Run SIMBA simulation
job = design.TransientAnalysis.NewJob()
status = job.Run()
print(job.Summary())
t = job.TimePoints
Ia = job.GetSignalByName('VA - Current').DataPoints
Ib = job.GetSignalByName('VB - Current').DataPoints
Ic = job.GetSignalByName('VC - Current').DataPoints
Te = job.GetSignalByName('JmagRT_PMSM - Te').DataPoints

# Convert time to miliseconds
t = [time * 1000 for time in t] # SIMBA
data_FEA['Time'] *= 1000  # FEA

========== 0 Error(s), 0 Warning(s) ==========
Job duration: 0.2897435 seconds.



## Results
The current and torque waveforms obtained from the FEA software and SIMBA are shown below. These waveforms are presented on individual graphs for easy comparison.

In [16]:
# Create a figure for the current waveform
current_plot = figure(title='Current Waveforms', x_axis_label='Time [ms]', y_axis_label='Current [A]', width = 800, height = 500, x_range = (0, max(t)))
# Plot FEA results
current_plot.line(data_FEA['Time'], data_FEA['FEA Ia [A]'], color ='red', legend_label='Ia (FEA)', width = 1.5)
current_plot.line(data_FEA['Time'], data_FEA['FEA Ib [A]'], color ='green', legend_label='Ib (FEA)', width = 1.5)
current_plot.line(data_FEA['Time'], data_FEA['FEA Ic [A]'], color ='blue', legend_label='Ic (FEA)', width = 1.5)
# Plot SIMBA results
current_plot.line(t, Ia, color = 'red', legend_label='Ia (SIMBA)', dash='dashed', width=2)
current_plot.line(t, Ib, color = 'green', legend_label='Ib (SIMBA)', dash='dashed', width=2)
current_plot.line(t, Ic, color = 'blue', legend_label='Ic (SIMBA)', dash='dashed', width=2)
# Graph customization
current_plot.title.align = 'center'
current_plot.legend.label_text_font_size = '10pt'
current_plot.legend.location = 'top_right'
current_plot.legend.click_policy = 'mute'
current_plot.legend.border_line_color = 'black'
current_plot.legend.background_fill_color = 'white'

# Create a figure for the torque waveform
torque_plot = figure(title='Torque Waveform', x_axis_label='Time [ms]', y_axis_label='Torque [Nm]', width = 800, height = 500, x_range = (0, max(t)), y_range = (0, 23))
# Plot FEA results
torque_plot.line(data_FEA['Time'], data_FEA['Torque [Nm]'], color='green', legend_label='FEA', width = 1.5)
# Plot SIMBA results
torque_plot.line(t, Te, color = 'red', legend_label='SIMBA', dash='dashed', width=1.5)
# Graph customization
torque_plot.title.align = 'center'
torque_plot.legend.label_text_font_size = '10pt'
torque_plot.legend.location = 'top_right'
torque_plot.legend.border_line_color = 'black'
torque_plot.legend.background_fill_color = 'white'

output_notebook()
# Option 1: Show figures in a single row
show(row(current_plot, torque_plot))
# Option2: Show figures in two rows
# show(current_plot)
# show(torque_plot)

Loading BokehJS ...

In the current waveform, it is observed that despite an ideal sinusoidal voltage input to the PMSM, the current waveform exhibits non-sinusoidal behavior. In addition, the torque waveform shows the presence of torque ripple. 
These deviations can be attributed to the influence of spatial harmonics.

# Conclusion

The validation above demonstrates that the simulation results of the JMAG-RT motor model match those obtained with the FEA software, thus confirming the accuracy of the PMSM model in SIMBA. Additionally, the JMAG-RT motor model demonstrates enhanced fidelity by accurately capturing realistic phenomena, including spatial harmonics, providing a more comprehensive representation of motor behavior.